In [1]:
import sys
sys.path.insert(0, '/Users/mvilenko/Library/CloudStorage/OneDrive-PayPal/hgru_clean/Norway/')

In [2]:
#importing all the required packages
import optuna

import torch
import pandas as pd
import numpy as np
import statistics
import torch
import random
import time
import numpy as np
#from transformers import AdamW
from torch.utils.tensorboard import SummaryWriter
import pickle
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
import torch.optim as optim
import shutil
import itertools
import os
from pathlib import Path

from model.GRU_model import *
from pipeline_config import *
from utils import *

/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
print(f'Features: {Features}')
print(f'HiddenSize: {HiddenSize}')
print(f'LayersDim: {LayersDim}')
print(f'OutputDim: {OutputDim}')
print(f'DropoutProb: {DropoutProb}')
print(f'Lr : {Lr}')
print(f'Epochs : {Epochs}')

Features: 1
HiddenSize: 64
LayersDim: 1
OutputDim: 1
DropoutProb: 0.0
Lr : 0.1
Epochs : 100


In [4]:
SequenceLength

12

In [5]:
def rmdir(dirc):
    dirc = Path(dirc)
    for itm in dirc.iterdir():
        if itm.is_dir():
            rmdir(itm)
            print("Deleting", itm, ".... successful.")
        else:
            itm.unlink()
    dirc.rmdir()

In [6]:
def objective(trial):
    with open(train_dataset_path, 'rb') as f:
        train_dataset_dict = pickle.load(f)
        
    with open(test_dataset_path, 'rb') as f:
        test_dataset_dict = pickle.load(f)

    with open(category_id_to_category_name_path, 'rb') as f:
        category_id_to_name_dict = pickle.load(f)
        
    with open(categories_per_indent_path, 'rb') as f:
        categories_per_indent_dict = pickle.load(f)

    with open(son_parent_path, 'rb') as f:
        son_parent_dict = pickle.load(f)

    with open(parent_to_son_list_path, 'rb') as f:
        parent_to_son_list_dict = pickle.load(f)

    with open(hgru_model_weights_path, 'rb') as f:
        hgru_weight_dict = pickle.load(f)

    with open(coefficient_dict_path, 'rb') as f:
        coefficient_dict = pickle.load(f)
    
    weights_path = weightspath

    #--------------------------------------------------------------------------------------------------------------------------------------#

    loss_coef_1 = trial.suggest_float('loss_coef_1',  1e-15, 1e-6, log=True)
    loss_coef_2 = trial.suggest_float('loss_coef_2',  1e-15, 1e-6, log=True)

    bi_directional_models = {}
    num_categories = 0

    for indent in sorted(list(categories_per_indent_dict.keys()),reverse=True):
        for category in categories_per_indent_dict[indent]:
            num_categories +=1
            print(f'num categories: {num_categories}')
            category_name = category_id_to_name_dict[category]
            print(f'category id|name: {category}|{category_name}')

            if int(indent) == 0 or son_parent_dict[category] not in categories_per_indent_dict[indent-1]: #or (category, son_parent_dict[category]) not in son_parent_corr_dict.keys():
                loss_coef_1 = 0

            if (category not in list(parent_to_son_list_dict.keys())) or (set(parent_to_son_list_dict[category]['sons']).issubset(set(categories_per_indent_dict[indent+1]))):
                loss_coef_2 = 0
 
            print('------------------------------------------------------------------')

            train_dataloader, test_dataloader = create_dataloader(train_dataset_dict[category_name], test_dataset_dict[category_name])
            model = GRUModel(input_dim=Features, hidden_dim=HiddenSize, layer_dim=LayersDim, output_dim=OutputDim, dropout_prob=DropoutProb, seed=0)
            optimizer = torch.optim.AdamW(model.parameters(), lr=Lr)
            model.to(Device)
            saving_param_path = weights_path+category_name+'.pt'
            
            min_error = training_and_evaluation(trial, model, indent, train_dataloader, test_dataloader, optimizer, category, hgru_weight_dict, coefficient_dict, son_parent_dict, parent_to_son_list_dict, category_id_to_name_dict, loss_coef_1, loss_coef_2, alpha, saving_param_path)
            
            bi_directional_models[category] = min_error

    average_error = sum(list(bi_directional_models.values()))/len(list(bi_directional_models.values()))
    
    return average_error


In [7]:
EPOCHS = 50
    
study = optuna.create_study(direction="minimize", sampler=optuna.samplers.GPSampler())
study.optimize(objective, n_trials=50)

/var/folders/88/mkn0vj0s1kl1179x22s6j2h80000gq/T/ipykernel_15977/2629109679.py:3: ExperimentalWarning: GPSampler is experimental (supported from v3.6.0). The interface can change in the future.
  study = optuna.create_study(direction="minimize", sampler=optuna.samplers.GPSampler())
[I 2024-09-01 22:28:29,431] A new study created in memory with name: no-name-21cca291-1528-451f-acf9-dcf91f1f4d82


num categories: 1
category id|name: 45|Accommodation services
------------------------------------------------------------------
num categories: 2
category id|name: 19|Actual rentals for housing
------------------------------------------------------------------


/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python

num categories: 3
category id|name: 15|Alcoholic beverages
------------------------------------------------------------------
num categories: 4
category id|name: 38|Audio-visual, photographic and information processing equipment
------------------------------------------------------------------
num categories: 5
category id|name: 17|Clothing
------------------------------------------------------------------
num categories: 6
category id|name: 23|Electricity, gas and other fuels
------------------------------------------------------------------
num categories: 7
category id|name: 50|Financial services n.e.c.
------------------------------------------------------------------
num categories: 8
category id|name: 13|Food
------------------------------------------------------------------
num categories: 9
category id|name: 18|Footwear
------------------------------------------------------------------
num categories: 10
category id|name: 24|Furniture and furnishings, carpets and other floor c

[I 2024-09-01 22:47:21,393] Trial 0 finished with value: 0.0193214377685473 and parameters: {'loss_coef_1': 1.7366813798758583e-08, 'loss_coef_2': 3.3326874732763534e-07}. Best is trial 0 with value: 0.0193214377685473.


...

[I 2024-09-02 05:53:26,733] Trial 48 finished with value: 0.01725551346109049 and parameters: {'loss_coef_1': 1.7999703703822222e-14, 'loss_coef_2': 1.0000000000000013e-15}. Best is trial 38 with value: 0.01710546028478567.


num categories: 1
category id|name: 45|Accommodation services
------------------------------------------------------------------
num categories: 2
category id|name: 19|Actual rentals for housing
------------------------------------------------------------------


/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python

num categories: 3
category id|name: 15|Alcoholic beverages
------------------------------------------------------------------
num categories: 4
category id|name: 38|Audio-visual, photographic and information processing equipment
------------------------------------------------------------------
num categories: 5
category id|name: 17|Clothing
------------------------------------------------------------------
num categories: 6
category id|name: 23|Electricity, gas and other fuels
------------------------------------------------------------------
num categories: 7
category id|name: 50|Financial services n.e.c.
------------------------------------------------------------------
num categories: 8
category id|name: 13|Food
------------------------------------------------------------------
num categories: 9
category id|name: 18|Footwear
------------------------------------------------------------------
num categories: 10
category id|name: 24|Furniture and furnishings, carpets and other floor c

[I 2024-09-02 06:01:05,975] Trial 49 finished with value: 0.01723313879443634 and parameters: {'loss_coef_1': 1.8010417994059727e-14, 'loss_coef_2': 1.0000000000000013e-15}. Best is trial 38 with value: 0.01710546028478567.


In [9]:
# Get the best trial
best_trial = study.best_trial

# Print the best trial
print('Best trial:')
print(f'Value: {best_trial.value}')
print('Parameters:')
for key, value in best_trial.params.items():
    print(f'{key}: {value}')

Best trial:
Value: 0.01710546028478567
Parameters:
loss_coef_1: 1.3614879789690235e-14
loss_coef_2: 1.0000000000000013e-15


In [10]:
EPOCHS = 50
    
study = optuna.create_study(direction="minimize", sampler=optuna.samplers.RandomSampler())
study.optimize(objective, n_trials=50)

[I 2024-09-02 06:01:06,075] A new study created in memory with name: no-name-adcbe48e-0da3-4f67-bef9-fa67c6b52133


num categories: 1
category id|name: 45|Accommodation services
------------------------------------------------------------------
num categories: 2
category id|name: 19|Actual rentals for housing
------------------------------------------------------------------


/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python

num categories: 3
category id|name: 15|Alcoholic beverages
------------------------------------------------------------------
num categories: 4
category id|name: 38|Audio-visual, photographic and information processing equipment
------------------------------------------------------------------
num categories: 5
category id|name: 17|Clothing
------------------------------------------------------------------
num categories: 6
category id|name: 23|Electricity, gas and other fuels
------------------------------------------------------------------
num categories: 7
category id|name: 50|Financial services n.e.c.
------------------------------------------------------------------
num categories: 8
category id|name: 13|Food
------------------------------------------------------------------
num categories: 9
category id|name: 18|Footwear
------------------------------------------------------------------
num categories: 10
category id|name: 24|Furniture and furnishings, carpets and other floor c

[I 2024-09-02 06:08:31,413] Trial 0 finished with value: 0.017786502477215287 and parameters: {'loss_coef_1': 9.153445857160888e-15, 'loss_coef_2': 7.085646258419619e-13}. Best is trial 0 with value: 0.017786502477215287.


...

[I 2024-09-02 14:21:52,683] Trial 48 finished with value: 0.01791035539213476 and parameters: {'loss_coef_1': 9.538128043141896e-08, 'loss_coef_2': 1.3926026983359183e-09}. Best is trial 46 with value: 0.01705909070397656.


num categories: 1
category id|name: 45|Accommodation services
------------------------------------------------------------------
num categories: 2
category id|name: 19|Actual rentals for housing
------------------------------------------------------------------


/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python

num categories: 3
category id|name: 15|Alcoholic beverages
------------------------------------------------------------------
num categories: 4
category id|name: 38|Audio-visual, photographic and information processing equipment
------------------------------------------------------------------
num categories: 5
category id|name: 17|Clothing
------------------------------------------------------------------
num categories: 6
category id|name: 23|Electricity, gas and other fuels
------------------------------------------------------------------
num categories: 7
category id|name: 50|Financial services n.e.c.
------------------------------------------------------------------
num categories: 8
category id|name: 13|Food
------------------------------------------------------------------
num categories: 9
category id|name: 18|Footwear
------------------------------------------------------------------
num categories: 10
category id|name: 24|Furniture and furnishings, carpets and other floor c

[I 2024-09-02 14:32:06,473] Trial 49 finished with value: 0.018868057964277544 and parameters: {'loss_coef_1': 6.277364720243553e-08, 'loss_coef_2': 1.968878367127523e-14}. Best is trial 46 with value: 0.01705909070397656.


In [11]:
# Get the best trial
best_trial = study.best_trial

# Print the best trial
print('Best trial:')
print(f'Value: {best_trial.value}')
print('Parameters:')
for key, value in best_trial.params.items():
    print(f'{key}: {value}')

Best trial:
Value: 0.01705909070397656
Parameters:
loss_coef_1: 2.5830392109982365e-12
loss_coef_2: 8.20579251220309e-15


In [12]:
EPOCHS = 50
    
study = optuna.create_study(direction="minimize", sampler=optuna.samplers.TPESampler())
study.optimize(objective, n_trials=50)

[I 2024-09-02 14:32:06,696] A new study created in memory with name: no-name-ed673c1e-cf0a-46ca-b625-9813501b753f


num categories: 1
category id|name: 45|Accommodation services
------------------------------------------------------------------
num categories: 2
category id|name: 19|Actual rentals for housing
------------------------------------------------------------------


/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python

num categories: 3
category id|name: 15|Alcoholic beverages
------------------------------------------------------------------
num categories: 4
category id|name: 38|Audio-visual, photographic and information processing equipment
------------------------------------------------------------------
num categories: 5
category id|name: 17|Clothing
------------------------------------------------------------------
num categories: 6
category id|name: 23|Electricity, gas and other fuels
------------------------------------------------------------------
num categories: 7
category id|name: 50|Financial services n.e.c.
------------------------------------------------------------------
num categories: 8
category id|name: 13|Food
------------------------------------------------------------------
num categories: 9
category id|name: 18|Footwear
------------------------------------------------------------------
num categories: 10
category id|name: 24|Furniture and furnishings, carpets and other floor c

[I 2024-09-02 14:41:12,080] Trial 0 finished with value: 0.018286666032029213 and parameters: {'loss_coef_1': 3.832762077314946e-10, 'loss_coef_2': 5.6197215824826916e-14}. Best is trial 0 with value: 0.018286666032029213.


...

[I 2024-09-02 23:25:18,811] Trial 48 finished with value: 0.017388579483619885 and parameters: {'loss_coef_1': 3.678928133187139e-15, 'loss_coef_2': 5.082246162441624e-12}. Best is trial 14 with value: 0.01689233522795673.


num categories: 1
category id|name: 45|Accommodation services
------------------------------------------------------------------
num categories: 2
category id|name: 19|Actual rentals for housing
------------------------------------------------------------------


/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python/site-packages/optuna/trial/_trial.py:493: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/Users/mvilenko/Library/Python/3.9/lib/python

num categories: 3
category id|name: 15|Alcoholic beverages
------------------------------------------------------------------
num categories: 4
category id|name: 38|Audio-visual, photographic and information processing equipment
------------------------------------------------------------------
num categories: 5
category id|name: 17|Clothing
------------------------------------------------------------------
num categories: 6
category id|name: 23|Electricity, gas and other fuels
------------------------------------------------------------------
num categories: 7
category id|name: 50|Financial services n.e.c.
------------------------------------------------------------------
num categories: 8
category id|name: 13|Food
------------------------------------------------------------------
num categories: 9
category id|name: 18|Footwear
------------------------------------------------------------------
num categories: 10
category id|name: 24|Furniture and furnishings, carpets and other floor c

[I 2024-09-02 23:35:29,956] Trial 49 finished with value: 0.019021401772209047 and parameters: {'loss_coef_1': 8.375822429614636e-09, 'loss_coef_2': 1.2876358294137734e-11}. Best is trial 14 with value: 0.01689233522795673.


In [13]:
# Get the best trial
best_trial = study.best_trial

# Print the best trial
print('Best trial:')
print(f'Value: {best_trial.value}')
print('Parameters:')
for key, value in best_trial.params.items():
    print(f'{key}: {value}')

Best trial:
Value: 0.01689233522795673
Parameters:
loss_coef_1: 3.743092554196371e-12
loss_coef_2: 4.015085187747426e-13
